## Bollinger Band ADX Strategy Backtesting

In [1]:
import yfinance as yf
import datetime as dt
import pandas as pd 
import numpy as np
import cufflinks as cf
from plotly.offline import download_plotlyjs,init_notebook_mode,plot,iplot
import plotly.graph_objects as go
from plotly.subplots import make_subplots

init_notebook_mode(connected = True)
cf.go_offline()

In [2]:
def calculate_ema(prices, days, smoothing=2):
    ema = [sum(prices[:days]) / days]
    for price in prices[days:]:
        ema.append((price * (smoothing / (1 + days))) + ema[-1] * (1 - (smoothing / (1 + days))))
    return ema

def adx(df_signal):
    df_signal['Close_t-1']=df_signal['Close'].shift(1)
    df_signal['High_t-1']=df_signal['High'].shift(1)
    df_signal['Low_t-1']=df_signal['Low'].shift(1)
    df_signal['ATR1'] = df_signal['High']-df_signal['Low']
    df_signal['ATR2'] = abs(df_signal['High']-df_signal['Close_t-1'])
    df_signal['ATR3'] = abs(df_signal['Low']-df_signal['Close_t-1'])
    df_signal['ATR']= df_signal[['ATR1','ATR2','ATR3']].max(axis=1)
    df_signal['TR14'] = df_signal['ATR'].rolling(14).sum()
    df_signal['plus_dm'] =np.NaN
    df_signal['minus_dm'] =np.NaN
    for i in range(1,len(df_signal)):
        h_minus_ph = df_signal['High'][i] - df_signal['High_t-1'][i]
        pl_minus_l = df_signal['Low_t-1'][i]-df_signal['Low'][i]
        if h_minus_ph > pl_minus_l:
            if h_minus_ph > 0:
                plus_dm = h_minus_ph
                minus_dm = 0
            else:
                plus_dm = 0
                minus_dm = 0
        else:
            if pl_minus_l > 0:
                plus_dm = 0
                minus_dm = pl_minus_l
            else:
                plus_dm = 0
                minus_dm = 0
        df_signal['plus_dm'][i] = plus_dm
        df_signal['minus_dm'][i] = minus_dm

    df_signal['plus_dm14'] = df_signal['plus_dm'].rolling(14).sum()
    df_signal['minus_dm14'] = df_signal['minus_dm'].rolling(14).sum()
    df_signal['plus_di14'] = df_signal['plus_dm14']*100/df_signal['TR14']
    df_signal['minus_di14'] = df_signal['minus_dm14']*100/df_signal['TR14']
    df_signal['diff_di14'] = abs(df_signal['plus_di14']-df_signal['minus_di14'])
    df_signal['sum_di14'] = abs(df_signal['plus_di14']+df_signal['minus_di14'])
    df_signal['DX'] = df_signal['diff_di14']*100/df_signal['sum_di14']
    df_signal['ADX'] = df_signal['DX'].rolling(14).mean()
    return df_signal

In [3]:
def bollinger_ADX_backtesting(ticker, previous_days):
    
    start = dt.datetime.today()-dt.timedelta(previous_days)
    end = dt.datetime.today()
    global ohlc_intraday
    ohlc_intraday = {}
    ohlc_intraday[ticker] = yf.download(ticker,start,end)
    ohlc_intraday[ticker] = ohlc_intraday[ticker].reset_index(drop = False)
    global df_signal
    df_signal = ohlc_intraday[ticker].copy()
    df_signal = df_signal[['Date','Open','High','Low','Close']]
    
    df_signal['sma']= df_signal['Close'].rolling(20).mean()
    df_signal['std'] = df_signal['Close'].rolling(20).std()
    df_signal['upper']= df_signal['sma'] + (2*df_signal['std'])
    df_signal['lower']= df_signal['sma'] - (2*df_signal['std'])

    adx(df_signal)
    
    df_signal['Low_t-2']=df_signal['Low'].shift(2)
    df_signal['lower_t-2']=df_signal['lower'].shift(2)
    df_signal['Close_t-1']=df_signal['Close'].shift(1)
    df_signal['lower_t-1']=df_signal['lower'].shift(1)

    condition_t_2 = (df_signal['Low_t-2']<df_signal['lower_t-2'])
    condition_t_1 = (df_signal['Close_t-1']>df_signal['lower_t-1']) 
    buy_condition = condition_t_1&condition_t_2
    df_signal['Buy']=np.where(buy_condition, 'Buy', '')
        
    df_signal = df_signal[['Date','Open','High','Low','Close','std','upper','lower','sma','ADX','Buy']]
    df_signal['Action'] = ''
    
    condition = (df_signal['Buy']=='Buy')
    df_signal2 = df_signal[condition].copy()
    df_signal2 = df_signal2.reset_index(drop = True)
    df_signal2 = df_signal2[['Date','Buy']]
    
    columns_Trading = ['Date_Buy','Price_Buy','Date_Sell','Price_Sell','PL(%)','Holding_Days','Accumulated profit']
    global df_Trading
    df_Trading = pd.DataFrame(columns = columns_Trading)
    
    Accu_profit = 0
    for i in range(len(df_signal2)):
        check_action = df_signal[df_signal['Date']==df_signal2['Date'][i]].reset_index()
        if check_action['Action'][0] =='':
            date_index = df_signal[df_signal['Date']==df_signal2['Date'][i]].index[0]
            Date_Buy = df_signal['Date'][date_index]
            Price_Buy = df_signal['Open'][date_index]
            stop_loss = 0.95*Price_Buy
            df_signal.loc[date_index,'Action']='Buy'
            date_index += 1
            stage = 'ToStop'
            close_order = False
            while True & (date_index < len(df_signal)):
                df_signal['Action'][date_index] = 'Hold'
                if stage == 'ToStop':
                    if (df_signal['Close'][date_index] < stop_loss) |(df_signal['Close'][date_index] < df_signal['lower'][date_index]):
                        close_order = True
                        break
                    elif df_signal['Close'][date_index] > Price_Buy:
                        stage = 'ToProfit'
                elif stage == 'ToProfit':  
                    if (df_signal['High'][date_index-1] > df_signal['upper'][date_index-1])&(df_signal['Close'][date_index] < df_signal['upper'][date_index]):
                        if df_signal['ADX'][date_index] >= 20:
                            stage = 'Trend'
                        else:
                            close_order = True
                            break
                    elif df_signal['Close'][date_index] < Price_Buy:
                        stage = 'ToStop'
                elif stage == 'Trend':
                    if df_signal['Close'][date_index] <=  df_signal['sma'][date_index]:
                        close_order = True
                        break 
                date_index += 1
                if date_index >= len(df_signal):
                    break
            if close_order:
                date_index += 1
                df_signal['Action'][date_index] = 'Sell'
                Date_Sell = df_signal['Date'][date_index]
                Price_Sell = df_signal['Open'][date_index]
                fee = 0.002*(Price_Sell+Price_Buy)
                PL = (Price_Sell-Price_Buy-fee)*100/Price_Buy
                Holding_Days = abs(Date_Sell-Date_Buy).days
                Accu_profit += PL

                Add_Trading = pd.DataFrame([[Date_Buy,Price_Buy,Date_Sell,Price_Sell,PL,Holding_Days,Accu_profit]],columns = columns_Trading)
                df_Trading = df_Trading.append(Add_Trading)

    df_Trading = df_Trading.reset_index(drop = True)
    df_Trading = df_Trading.round(2)
    
    total_profit = df_Trading['Accumulated profit'][len(df_Trading)-1]
    cagr = ((((total_profit+100)/100)**(1/(len(df_signal)/250)))-1)*100
    win_trade = df_Trading[df_Trading["PL(%)"]>0].count()["PL(%)"]
    loss_trade =  df_Trading[df_Trading["PL(%)"]<=0].count()["PL(%)"]
    win_rate = win_trade*100/(win_trade+loss_trade)
    avg_gain = df_Trading[df_Trading["PL(%)"]>0]["PL(%)"].mean()
    avg_loss = df_Trading[df_Trading["PL(%)"]<=0]["PL(%)"].mean()
    expected_return = (win_rate*avg_gain/100)+((1-win_rate)*avg_loss/100)
    
    list_ = [["Total Profit",round(total_profit,2)],
            ["CAGR",str(round(cagr,2))+'%'],
             ["Win Trade",win_trade],["Loss Trade ",loss_trade],
             ["Win Rate",str(round(win_rate,2))+'%'],["Average Gain",str(round(avg_gain,2))+'%'],
             ["Average loss",str(round(avg_loss,2))+'%'],["Expected Return",str(round(expected_return,2))+'%']]
                      
    global df_summary
    df_summary = pd.DataFrame(list_,columns=['Measurement','Result'])
    
    
def plot_bollinger_ADX():

    fig = make_subplots(rows=4, cols=1,shared_xaxes=True, vertical_spacing=0.04,
    specs=[[{"type": "scatter"}],[{"type": "scatter"}],
          [{"type": "table"}],[{"type": "table"}]])

    buy = df_Trading[['Date_Buy','Price_Buy']].copy()
    sell = df_Trading[['Date_Sell','Price_Sell']].copy()
    df_signal['20'] = 20
    
    fig.add_trace(go.Candlestick(x=df_signal['Date'],
                open=df_signal['Open'],
                high=df_signal['High'],
                low=df_signal['Low'],
                close=df_signal['Close']),row=1,col=1)

    #fig.add_trace(go.Scatter(x = df_signal['Date'], y=df_signal['Close'],mode='lines',name='Close'),row= 1,col =1)
    fig.add_trace(go.Scatter(x = df_signal['Date'], y=df_signal['upper'],mode='lines',name='upper'),row= 1,col =1)
    fig.add_trace(go.Scatter(x = df_signal['Date'], y=df_signal['lower'],mode='lines',name='lower'),row= 1,col =1)
    fig.add_trace(go.Scatter(x = df_signal['Date'], y=df_signal['sma'],mode='lines',name='sma'),row= 1,col =1)
    fig.add_trace(go.Scatter(x = buy['Date_Buy'], y=buy['Price_Buy'],mode='markers',name='buy'),row= 1,col =1)
    fig.add_trace(go.Scatter(x = sell['Date_Sell'], y=sell['Price_Sell'],mode='markers',name='sell'),row= 1,col =1)

    fig.add_trace(go.Scatter(x = df_signal['Date'], y=df_signal['ADX'],mode='lines',name='ADX'),row= 2,col =1)
    fig.add_trace(go.Scatter(x = df_signal['Date'], y=df_signal['20'],mode='lines',name='20'),row= 2,col =1)
    
    fig.add_trace(go.Table(header=dict(values=df_summary.columns,font=dict(size=10),align="left"),
            cells=dict(values=[df_summary[k].tolist() for k in df_summary.columns],align = "left")),row=3, col=1)

    fig.add_trace(go.Table(header=dict(values=df_Trading.columns,font=dict(size=10),align="left"),
            cells=dict(values=[df_Trading[k].tolist() for k in df_Trading.columns],align = "left")),row=4, col=1)

    fig.update_layout( height=1200, showlegend=True, title_text='Bollinger Band + ADX',)
    fig.update_layout(xaxis_rangeslider_visible=False)
    
    fig.show()

In [4]:
ticker = 'AAPL'
bollinger_ADX_backtesting(ticker, previous_days = 4000)

[*********************100%***********************]  1 of 1 completed


In [5]:
plot_bollinger_ADX()

In [6]:
# 1. Download Date from yfinance
ticker = 'AAPL'
start = dt.datetime.today()-dt.timedelta(4000)
end = dt.datetime.today()
ohlc_intraday = {}
ohlc_intraday[ticker] = yf.download(ticker,start,end)
ohlc_intraday[ticker] = ohlc_intraday[ticker].reset_index(drop = False)
df_signal = ohlc_intraday[ticker].copy()
df_signal

[*********************100%***********************]  1 of 1 completed


Date        Open        High         Low       Close   Adj Close  \
0    2011-01-04   11.872857   11.875000   11.719643   11.831786   10.144161   
1    2011-01-05   11.769643   11.940714   11.767857   11.928571   10.227139   
2    2011-01-06   11.954286   11.973214   11.889286   11.918929   10.218874   
3    2011-01-07   11.928214   12.012500   11.853571   12.004286   10.292058   
4    2011-01-10   12.101071   12.258214   12.041786   12.230357   10.485879   
...         ...         ...         ...         ...         ...         ...   
2753 2021-12-10  175.210007  179.630005  174.690002  179.449997  179.449997   
2754 2021-12-13  181.119995  182.130005  175.529999  175.740005  175.740005   
2755 2021-12-14  175.250000  177.740005  172.210007  174.330002  174.330002   
2756 2021-12-15  175.110001  179.500000  172.309998  179.300003  179.300003   
2757 2021-12-16  179.279999  181.139999  170.750000  172.259995  172.259995   

         Volume  
0     309080800  
1     255519600  
2     300428800  
3     311931200  
4     448560000  
...         ...  
2753  115228100  
2754  153237000  
2755  139380400  
2756  131063300  
2757  149964200  

[2758 rows x 7 columns]

In [7]:
# 2.remove some columns
df_signal = df_signal[['Date','Open','High','Low','Close']]
df_signal

Date        Open        High         Low       Close
0    2011-01-04   11.872857   11.875000   11.719643   11.831786
1    2011-01-05   11.769643   11.940714   11.767857   11.928571
2    2011-01-06   11.954286   11.973214   11.889286   11.918929
3    2011-01-07   11.928214   12.012500   11.853571   12.004286
4    2011-01-10   12.101071   12.258214   12.041786   12.230357
...         ...         ...         ...         ...         ...
2753 2021-12-10  175.210007  179.630005  174.690002  179.449997
2754 2021-12-13  181.119995  182.130005  175.529999  175.740005
2755 2021-12-14  175.250000  177.740005  172.210007  174.330002
2756 2021-12-15  175.110001  179.500000  172.309998  179.300003
2757 2021-12-16  179.279999  181.139999  170.750000  172.259995

[2758 rows x 5 columns]

In [8]:
# 3.Add std,upper band, lower band, sma ,adx
df_signal['sma']= df_signal['Close'].rolling(20).mean()
df_signal['std'] = df_signal['Close'].rolling(20).std()
df_signal['upper']= df_signal['sma'] + (2*df_signal['std'])
df_signal['lower']= df_signal['sma'] - (2*df_signal['std'])

adx(df_signal)

df_signal

Date        Open        High         Low       Close         sma  \
0    2011-01-04   11.872857   11.875000   11.719643   11.831786         NaN   
1    2011-01-05   11.769643   11.940714   11.767857   11.928571         NaN   
2    2011-01-06   11.954286   11.973214   11.889286   11.918929         NaN   
3    2011-01-07   11.928214   12.012500   11.853571   12.004286         NaN   
4    2011-01-10   12.101071   12.258214   12.041786   12.230357         NaN   
...         ...         ...         ...         ...         ...         ...   
2753 2021-12-10  175.210007  179.630005  174.690002  179.449997  162.279001   
2754 2021-12-13  181.119995  182.130005  175.529999  175.740005  163.566501   
2755 2021-12-14  175.250000  177.740005  172.210007  174.330002  164.783001   
2756 2021-12-15  175.110001  179.500000  172.309998  179.300003  166.198001   
2757 2021-12-16  179.279999  181.139999  170.750000  172.259995  167.136501   

           std       upper       lower   Close_t-1  ...   plus_dm  minus_dm  \
0          NaN         NaN         NaN         NaN  ...       NaN       NaN   
1          NaN         NaN         NaN   11.831786  ...  0.065714  0.000000   
2          NaN         NaN         NaN   11.928571  ...  0.032500  0.000000   
3          NaN         NaN         NaN   11.918929  ...  0.039286  0.000000   
4          NaN         NaN         NaN   12.004286  ...  0.245714  0.000000   
...        ...         ...         ...         ...  ...       ...       ...   
2753  8.210813  178.700627  145.857375  174.559998  ...  2.880005  0.000000   
2754  8.201276  179.969053  147.163948  179.449997  ...  2.500000  0.000000   
2755  7.881234  180.545470  149.020532  175.740005  ...  0.000000  3.319992   
2756  7.816619  181.831238  150.564764  174.330002  ...  1.759995  0.000000   
2757  7.321669  181.779839  152.493162  179.300003  ...  1.639999  0.000000   

      plus_dm14  minus_dm14  plus_di14  minus_di14  diff_di14   sum_di14  \
0           NaN         NaN        NaN         NaN        NaN        NaN   
1           NaN         NaN        NaN         NaN        NaN        NaN   
2           NaN         NaN        NaN         NaN        NaN        NaN   
3           NaN         NaN        NaN         NaN        NaN        NaN   
4           NaN         NaN        NaN         NaN        NaN        NaN   
...         ...         ...        ...         ...        ...        ...   
2753  30.300003   11.949997  43.666210   17.221486  26.444724  60.887696   
2754  28.120010   11.949997  39.695070   16.868983  22.826087  56.564053   
2755  28.120010   13.329987  38.190943   18.104003  20.086940  56.294946   
2756  29.540009   13.329987  37.717044   17.019890  20.697154  54.736933   
2757  31.180008   10.049988  37.507505   12.089476  25.418029  49.596981   

             DX        ADX  
0           NaN        NaN  
1           NaN        NaN  
2           NaN        NaN  
3           NaN        NaN  
4           NaN        NaN  
...         ...        ...  
2753  43.431967  47.275603  
2754  40.354406  45.192279  
2755  35.681604  43.872057  
2756  37.812045  42.721795  
2757  51.249145  43.728732  

[2758 rows x 27 columns]

In [9]:
# 4. Find long 'buy' day

df_signal['Low_t-2']=df_signal['Low'].shift(2)
df_signal['lower_t-2']=df_signal['lower'].shift(2)
df_signal['Close_t-1']=df_signal['Close'].shift(1)
df_signal['lower_t-1']=df_signal['lower'].shift(1)

condition_t_2 = (df_signal['Low_t-2']<df_signal['lower_t-2'])
condition_t_1 = (df_signal['Close_t-1']>df_signal['lower_t-1']) 

buy_condition = (condition_t_2) & (condition_t_1) 
df_signal['Buy']=np.where(buy_condition, 'Buy', '')

df_signal

Date        Open        High         Low       Close         sma  \
0    2011-01-04   11.872857   11.875000   11.719643   11.831786         NaN   
1    2011-01-05   11.769643   11.940714   11.767857   11.928571         NaN   
2    2011-01-06   11.954286   11.973214   11.889286   11.918929         NaN   
3    2011-01-07   11.928214   12.012500   11.853571   12.004286         NaN   
4    2011-01-10   12.101071   12.258214   12.041786   12.230357         NaN   
...         ...         ...         ...         ...         ...         ...   
2753 2021-12-10  175.210007  179.630005  174.690002  179.449997  162.279001   
2754 2021-12-13  181.119995  182.130005  175.529999  175.740005  163.566501   
2755 2021-12-14  175.250000  177.740005  172.210007  174.330002  164.783001   
2756 2021-12-15  175.110001  179.500000  172.309998  179.300003  166.198001   
2757 2021-12-16  179.279999  181.139999  170.750000  172.259995  167.136501   

           std       upper       lower   Close_t-1  ...  plus_di14  \
0          NaN         NaN         NaN         NaN  ...        NaN   
1          NaN         NaN         NaN   11.831786  ...        NaN   
2          NaN         NaN         NaN   11.928571  ...        NaN   
3          NaN         NaN         NaN   11.918929  ...        NaN   
4          NaN         NaN         NaN   12.004286  ...        NaN   
...        ...         ...         ...         ...  ...        ...   
2753  8.210813  178.700627  145.857375  174.559998  ...  43.666210   
2754  8.201276  179.969053  147.163948  179.449997  ...  39.695070   
2755  7.881234  180.545470  149.020532  175.740005  ...  38.190943   
2756  7.816619  181.831238  150.564764  174.330002  ...  37.717044   
2757  7.321669  181.779839  152.493162  179.300003  ...  37.507505   

      minus_di14  diff_di14   sum_di14         DX        ADX     Low_t-2  \
0            NaN        NaN        NaN        NaN        NaN         NaN   
1            NaN        NaN        NaN        NaN        NaN         NaN   
2            NaN        NaN        NaN        NaN        NaN   11.719643   
3            NaN        NaN        NaN        NaN        NaN   11.767857   
4            NaN        NaN        NaN        NaN        NaN   11.889286   
...          ...        ...        ...        ...        ...         ...   
2753   17.221486  26.444724  60.887696  43.431967  47.275603  170.699997   
2754   16.868983  22.826087  56.564053  40.354406  45.192279  173.919998   
2755   18.104003  20.086940  56.294946  35.681604  43.872057  174.690002   
2756   17.019890  20.697154  54.736933  37.812045  42.721795  175.529999   
2757   12.089476  25.418029  49.596981  51.249145  43.728732  172.210007   

       lower_t-2   lower_t-1  Buy  
0            NaN         NaN       
1            NaN         NaN       
2            NaN         NaN       
3            NaN         NaN       
4            NaN         NaN       
...          ...         ...  ...  
2753  144.292139  145.181977       
2754  145.181977  145.857375       
2755  145.857375  147.163948       
2756  147.163948  149.020532       
2757  149.020532  150.564764       

[2758 rows x 31 columns]

In [10]:
# 5. remove some columns and add 'Action' column
df_signal = df_signal[['Date','Open','High','Low','Close','std','upper','lower','sma','ADX','Buy']]
df_signal['Action'] = ''
df_signal

Date        Open        High         Low       Close       std  \
0    2011-01-04   11.872857   11.875000   11.719643   11.831786       NaN   
1    2011-01-05   11.769643   11.940714   11.767857   11.928571       NaN   
2    2011-01-06   11.954286   11.973214   11.889286   11.918929       NaN   
3    2011-01-07   11.928214   12.012500   11.853571   12.004286       NaN   
4    2011-01-10   12.101071   12.258214   12.041786   12.230357       NaN   
...         ...         ...         ...         ...         ...       ...   
2753 2021-12-10  175.210007  179.630005  174.690002  179.449997  8.210813   
2754 2021-12-13  181.119995  182.130005  175.529999  175.740005  8.201276   
2755 2021-12-14  175.250000  177.740005  172.210007  174.330002  7.881234   
2756 2021-12-15  175.110001  179.500000  172.309998  179.300003  7.816619   
2757 2021-12-16  179.279999  181.139999  170.750000  172.259995  7.321669   

           upper       lower         sma        ADX Buy Action  
0            NaN         NaN         NaN        NaN             
1            NaN         NaN         NaN        NaN             
2            NaN         NaN         NaN        NaN             
3            NaN         NaN         NaN        NaN             
4            NaN         NaN         NaN        NaN             
...          ...         ...         ...        ...  ..    ...  
2753  178.700627  145.857375  162.279001  47.275603             
2754  179.969053  147.163948  163.566501  45.192279             
2755  180.545470  149.020532  164.783001  43.872057             
2756  181.831238  150.564764  166.198001  42.721795             
2757  181.779839  152.493162  167.136501  43.728732             

[2758 rows x 12 columns]

In [11]:
# 6. filter days 'buy' signal 
condition = (df_signal['Buy']=='Buy')
df_signal2 = df_signal[condition].copy()
df_signal2 = df_signal2.reset_index(drop = True)
df_signal2 = df_signal2[['Date','Buy']]
df_signal2

Date  Buy
0   2011-03-18  Buy
1   2011-03-21  Buy
2   2011-03-22  Buy
3   2011-04-20  Buy
4   2011-05-18  Buy
..         ...  ...
155 2021-03-02  Buy
156 2021-05-07  Buy
157 2021-05-10  Buy
158 2021-05-14  Buy
159 2021-09-22  Buy

[160 rows x 2 columns]

In [12]:
# 7. Make trading dataframe
columns_Trading = ['Date_Buy','Price_Buy','Date_Sell','Price_Sell','PL(%)','Holding_Days','Accumulated profit']
df_Trading = pd.DataFrame(columns = columns_Trading)
df_Trading

Empty DataFrame
Columns: [Date_Buy, Price_Buy, Date_Sell, Price_Sell, PL(%), Holding_Days, Accumulated profit]
Index: []

In [13]:
# 8.Trading loop and record in df_Trading
Accu_profit = 0
for i in range(len(df_signal2)):
    check_action = df_signal[df_signal['Date']==df_signal2['Date'][i]].reset_index()
    if check_action['Action'][0] =='':
        date_index = df_signal[df_signal['Date']==df_signal2['Date'][i]].index[0]
        Date_Buy = df_signal['Date'][date_index]
        Price_Buy = df_signal['Open'][date_index]
        stop_loss = 0.92*Price_Buy
        df_signal.loc[date_index,'Action']='Buy'
        date_index += 1
        stage = 'ToStop'
        close_order = False
        while True & (date_index < len(df_signal)):
            df_signal['Action'][date_index] = 'Hold'
            if stage == 'ToStop':
                if (df_signal['Close'][date_index] < stop_loss) | \
                (df_signal['Close'][date_index] < df_signal['lower'][date_index]):
                    close_order = True
                    break
                elif df_signal['Close'][date_index] > Price_Buy:
                    stage = 'ToProfit'
            elif stage == 'ToProfit':  
                if (df_signal['High'][date_index-1] > df_signal['upper'][date_index-1])& \
                (df_signal['Close'][date_index] < df_signal['upper'][date_index]):
                    if df_signal['ADX'][date_index] >= 20:
                        stage = 'Trend'
                    else:
                        close_order = True
                        break
                elif df_signal['Close'][date_index] < Price_Buy:
                    stage = 'ToStop'
            elif stage == 'Trend':
                if df_signal['Close'][date_index] <=  df_signal['sma'][date_index]:
                    close_order = True
                    break 
            date_index += 1
            if date_index >= len(df_signal):
                break
        if close_order:
            date_index += 1
            df_signal['Action'][date_index] = 'Sell'
            Date_Sell = df_signal['Date'][date_index]
            Price_Sell = df_signal['Open'][date_index]
            fee = 0.002*(Price_Sell+Price_Buy)
            PL = (Price_Sell-Price_Buy-fee)*100/Price_Buy
            Holding_Days = abs(Date_Sell-Date_Buy).days
            Accu_profit += PL
            
            Add_Trading = pd.DataFrame([[Date_Buy,Price_Buy,Date_Sell,Price_Sell,PL
                            ,Holding_Days,Accu_profit]],columns = columns_Trading)
            df_Trading = df_Trading.append(Add_Trading)
            
df_Trading = df_Trading.reset_index(drop = True)
df_Trading = df_Trading.round(2)
df_Trading

Date_Buy  Price_Buy  Date_Sell  Price_Sell  PL(%) Holding_Days  \
0  2011-03-18      12.04 2011-06-13       11.69  -3.34           87   
1  2011-06-14      11.79 2011-06-21       11.31  -4.43            7   
2  2011-06-22      11.61 2011-08-05       13.59  16.57           44   
3  2011-10-06      13.33 2012-04-16       21.79  62.88          193   
4  2012-04-18      21.92 2012-04-23       20.38  -7.41            5   
..        ...        ...        ...         ...    ...          ...   
64 2021-02-22     128.01 2021-02-26      122.59  -4.63            4   
65 2021-03-01     123.75 2021-04-13      132.44   6.61           43   
66 2021-05-07     130.85 2021-05-11      123.50  -6.01            4   
67 2021-05-14     126.25 2021-06-10      127.02   0.21           27   
68 2021-09-22     144.45 2021-11-11      148.96   2.72           50   

    Accumulated profit  
0                -3.34  
1                -7.77  
2                 8.80  
3                71.68  
4                64.27  
..                 ...  
64              160.60  
65              167.21  
66              161.20  
67              161.41  
68              164.13  

[69 rows x 7 columns]

In [14]:
#9. Trading Summary
total_profit = df_Trading['Accumulated profit'][len(df_Trading)-1]
cagr = ((((total_profit+100)/100)**(1/(len(df_signal)/250)))-1)*100
win_trade = df_Trading[df_Trading["PL(%)"]>0].count()["PL(%)"]
loss_trade =  df_Trading[df_Trading["PL(%)"]<=0].count()["PL(%)"]
win_rate = win_trade*100/(win_trade+loss_trade)
avg_gain = df_Trading[df_Trading["PL(%)"]>0]["PL(%)"].mean()
avg_loss = df_Trading[df_Trading["PL(%)"]<=0]["PL(%)"].mean()
expected_return = (win_rate*avg_gain/100)+((1-win_rate)*avg_loss/100)
list_ = [["Total Profit",round(total_profit,2)],
            ["CAGR",str(round(cagr,2))+'%'],
             ["Win Trade",win_trade],["Loss Trade ",loss_trade],
             ["Win Rate",str(round(win_rate,2))+'%'],["Average Gain",str(round(avg_gain,2))+'%'],
             ["Average loss",str(round(avg_loss,2))+'%'],["Expected Return",str(round(expected_return,2))+'%']]

df_summary = pd.DataFrame(list_,columns=['Measurement','Result'])
df_summary

Measurement  Result
0     Total Profit  164.13
1             CAGR    9.2%
2        Win Trade      33
3      Loss Trade       36
4         Win Rate  47.83%
5     Average Gain  11.73%
6     Average loss  -6.19%
7  Expected Return   8.51%

In [15]:
#10.Plot graph

fig = make_subplots(
rows=4, cols=1,
shared_xaxes=True,
vertical_spacing=0.04,
specs=[[{"type": "scatter"}],[{"type": "scatter"}],
          [{"type": "table"}],[{"type": "table"}]])

buy = df_Trading[['Date_Buy','Price_Buy']].copy()
sell = df_Trading[['Date_Sell','Price_Sell']].copy()
df_signal['20'] = 20

fig.add_trace(go.Candlestick(x=df_signal['Date'],
                open=df_signal['Open'],
                high=df_signal['High'],
                low=df_signal['Low'],
                close=df_signal['Close']),row=1,col=1)

#fig.add_trace(go.Scatter(x = df_signal['Date'], y=df_signal['Close'],mode='lines',name='Close'),row= 1,col =1)
fig.add_trace(go.Scatter(x = df_signal['Date'], y=df_signal['upper'],mode='lines',name='upper'),row= 1,col =1)
fig.add_trace(go.Scatter(x = df_signal['Date'], y=df_signal['lower'],mode='lines',name='lower'),row= 1,col =1)
fig.add_trace(go.Scatter(x = df_signal['Date'], y=df_signal['sma'],mode='lines',name='sma'),row= 1,col =1)
fig.add_trace(go.Scatter(x = buy['Date_Buy'], y=buy['Price_Buy'],mode='markers',name='buy'),row= 1,col =1)
fig.add_trace(go.Scatter(x = sell['Date_Sell'], y=sell['Price_Sell'],mode='markers',name='sell'),row= 1,col =1)

fig.add_trace(go.Scatter(x = df_signal['Date'], y=df_signal['ADX'],mode='lines',name='ADX'),row= 2,col =1)
fig.add_trace(go.Scatter(x = df_signal['Date'], y=df_signal['20'],mode='lines',name='20'),row= 2,col =1)
    
fig.add_trace(go.Table(header=dict(values=df_summary.columns,font=dict(size=10),align="left"),
              cells=dict(values=[df_summary[k].tolist() for k in df_summary.columns],align = "left")),row=3, col=1)

fig.add_trace(go.Table(header=dict(values=df_Trading.columns,font=dict(size=10),align="left"),
              cells=dict(values=[df_Trading[k].tolist() for k in df_Trading.columns],align = "left")),row=4, col=1)

fig.update_layout( height=1200,  showlegend=True, title_text='Bollinger Band + ADX')
fig.update_layout(xaxis_rangeslider_visible=False)
fig.show()